# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model loaded [MaskablePPO]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import MaskablePPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env
from sb3_contrib.common.maskable.evaluation import evaluate_policy

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.21.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.21.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.21.0\n')
wandb, version 0.13.3


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f6517b5ef50>Mean parking time: 23.9
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.9, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energy

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20910.52 , over-consume=kWh  38222.15 , under-consume=kWh  17311.63 , Total_cost=€  827.7 , overcost=€  1340.8 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
%env "WANDB_DISABLE_CODE" True
%env "WANDB_NOTEBOOK_NAME" "Simulator_notebooks/MaskablePPO_VPP_simulator.ipynb"
os.environ['WANDB_NOTEBOOK_NAME'] = 'Simulator_notebooks/MaskablePPO_VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

env: "WANDB_DISABLE_CODE"=True
env: "WANDB_NOTEBOOK_NAME"="MaskablePPO_VPP_simulator.ipynb"


In [ ]:
#Loading training model, from local directory or from wandb previous trainings
MaskablePPO_path = "trained_models/MaskablePPO_models/model_MaskablePPO_"

model_id = "8mq440dz"
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21445.04 , over-consume=kWh  39090.56 , under-consume=kWh  17645.52 , Total_cost=€  857.27 , overcost=€  1366.64 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10675.55 , over-consume=KWh  1769.71 , under-consume=KWh  12445.26 , Total_cost=€  -260.3 , Overcost=€  66.52 
 EV_INFO: Av.EV_energy_leaving=kWh  59.92 , Std.EV_energy_leaving=kWh  21.93 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 227422.58 - Step_rewars (load_t= 230955.35, EVs_energy_t= -9601.45)
 - Final_rewards (EVs_energy= 5822.94, Overconsume= -1031.51, Underconsume= -9474.24, Overcost= 10751.48)
Episode:1 Score:227422.57935323697


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000  45.797501  46.451054  33.438339   
2022-01-01 00:15:00   0.000000  45.797501  46.451054  33.438339   
2022-01-01 00:30:00   0.000000  45.797501  46.451054  32.844616   
2022-01-01 00:45:00   0.000000  45.797501  46.451054  32.433231   
2022-01-01 01:00:00   0.000000  45.797501  46.451054  32.099934   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  55.595474  79.490295  75.753067  57.593281   
2022-06-06 05:00:00  56.672295  80.567116  76.829887  57.593281   
2022-06-06 05:15:00  57.663868  81.558693  77.821465  57.593281   
2022-06-06 05:30:00  58.628803  82.523628  78.786400  57.593281   
2022-06-06 05:45:00  59.685532  83.580360  79.843132  57.593281   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:15:00     [0, 3128, 3127, 3129]  [0, 0, 0, 2]   
2022-01-01 00:30:00     [0, 3128, 3127, 3129]  [0, 0, 0, 2]   
2022-01-01 00:45:00     [0, 3128, 3127, 3129]  [0, 0, 0, 2]   
2022-01-01 01:00:00     [0, 3128, 3127, 3129]  [0, 0, 0, 2]   
...                                       ...           ...   
2022-06-06 04:45:00  [3556, 3553, 3554, 3555]  [1, 1, 1, 0]   
2022-06-06 05:00:00  [3556, 3553, 3554, 3555]  [1, 1, 1, 0]   
2022-06-06 05:15:00  [3556, 3553, 3554, 3555]  [1, 1, 1, 0]   
2022-06-06 05:30:00  [3556, 3553, 3554, 3555]  [1, 1, 1, 0]   
2022-06-06 05:45:00  [3556, 3553, 3554, 3555]  [1, 1, 1, 0]   

                                    mask_truth          load  load_reward  \
time                                                                        
2022-01-01 00:00:00   [True, True, True, True]  1.427185e+00    -4.151562   
2022-01-01 00:15:00  [True, True, False, True]  2.990937e+00    15.000000   
2022-01-01 00:30:00  [True, True, False, True]  0.000000e+00    15.000000   
2022-01-01 00:45:00  [True, True, False, True]  0.000000e+00    15.000000   
2022-01-01 01:00:00  [True, True, False, True]  0.000000e+00    11.966941   
...                                        ...           ...          ...   
2022-06-06 04:45:00   [True, True, True, True]  0.000000e+00    15.000000   
2022-06-06 05:00:00   [True, True, True, True]  0.000000e+00    15.000000   
2022-06-06 05:15:00  [True, True, True, False]  0.000000e+00    15.000000   
2022-06-06 05:30:00  [True, True, True, False]  0.000000e+00    15.000000   
2022-06-06 05:45:00  [True, True, True, False]  1.776357e-15    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.151562  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  11.966941  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 17:45:00, Parking_time: 23.577299277002073, Leaving_time: 2022-01-02 17:19:38.277397, SOC: 0.640532067797412, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2023-01-01 00:00:00, Parking_time: 23.55953376594887, Leaving_time: 2023-01-01 23:33:34.321557, SOC: 0.40745372179655387, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12781.8 , over-consume=kWh  34639.05 , under-consume=kWh  21857.26 , Total_cost=€  636.04 , overcost=€  1522.91 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11743.5 , over-consume=kWh  33481.0 , under-consume=kWh  21737.49 , Total_cost=€  589.33 , overcost=€  1465.08 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -13633.82 , over-consume=KWh  1263.92 , under-consume=KWh  14897.74 , Total_cost=€  -537.34 , Overcost=€  55.57 
 EV_INFO: Av.EV_energy_leaving=kWh  66.0 , Std.EV_energy_leaving=kWh  20.66 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 227920.56 - Step_rewars (load_t= 199511.17, EVs_energy_t= 14728.39)
 - Final_rewards (EVs_energy= 10712.31, Overconsume= -724.5, Underconsume= -9100.27, Overcost= 12793.45)
Episode:1 Score:227920.56040985376


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  95.655777  35.581085  91.478264  65.477875   
2022-06-06 05:00:00  95.655777  35.581085  94.228264  65.477875   
2022-06-06 05:15:00  95.655777  35.581085  96.978264  65.477875   
2022-06-06 05:30:00  95.655777  35.581085  99.728264  65.477875   
2022-06-06 05:45:00  95.655777  35.581085  99.989998  65.477875   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [0, 0, 0, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [6717, 6720, 6719, 6718]  [0, 0, 1, 0]   
2022-06-06 05:00:00  [6717, 6720, 6719, 6718]  [0, 0, 1, 0]   
2022-06-06 05:15:00  [6717, 6720, 6719, 6718]  [0, 0, 1, 0]   
2022-06-06 05:30:00  [6717, 6720, 6719, 6718]  [0, 0, 1, 0]   
2022-06-06 05:45:00  [6717, 6720, 6719, 6718]  [0, 0, 1, 0]   

                                     mask_truth       load  load_reward  \
time                                                                      
2022-01-01 00:00:00    [True, True, True, True]  -3.251168    -5.053101   
2022-01-01 00:15:00    [True, True, True, True]  -4.058411    -4.661592   
2022-01-01 00:30:00    [True, True, True, True]  -3.796955    -3.203447   
2022-01-01 00:45:00    [True, True, True, True]  -2.922068    -5.143100   
2022-01-01 01:00:00    [True, True, True, True]  -4.157410    -3.455557   
...                                         ...        ...          ...   
2022-06-06 04:45:00  [True, False, False, True]   0.000000    -3.776205   
2022-06-06 05:00:00  [True, False, False, True]  -3.265723    -3.309420   
2022-06-06 05:15:00  [True, False, False, True]  -2.985652    -3.467406   
2022-06-06 05:30:00  [True, False, False, True]  -3.080444   -12.961718   
2022-06-06 05:45:00  [True, False, False, True] -12.757889   -15.808135   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.053101  
2022-01-01 00:15:00        0.0  -4.661592  
2022-01-01 00:30:00        0.0  -3.203447  
2022-01-01 00:45:00        0.0  -5.143100  
2022-01-01 01:00:00        0.0  -3.455557  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -3.776205  
2022-06-06 05:00:00        0.0  -3.309420  
2022-06-06 05:15:00        0.0  -3.467406  
2022-06-06 05:30:00        0.0 -12.961718  
2022-06-06 05:45:00        0.0 -15.808135  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 15:00:00, Parking_time: 24, Leaving_time: 2022-01-02 15:00:00, SOC: 0.5289107056930702, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 23:15:00, Parking_time: 23.124422596136068, Leaving_time: 2023-01-01 22:22:27.921346, SOC: 0.444558383356411, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8367.53 , over-consume=kWh  31423.63 , under-consume=kWh  23056.1 , Total_cost=€  492.25 , overcost=€  1323.51 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = MaskablePPO.load(MaskablePPO_path + model_id, env=env)

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, action_masks=action_masks, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  9443.17 , over-consume=kWh  32616.57 , under-consume=kWh  23173.4 , Total_cost=€  523.59 , overcost=€  1374.74 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -15364.55 , over-consume=KWh  957.49 , under-consume=KWh  16322.04 , Total_cost=€  -542.67 , Overcost=€  39.67 
 EV_INFO: Av.EV_energy_leaving=kWh  67.57 , Std.EV_energy_leaving=kWh  21.4 , EV_departures =  1038 , EV_queue_left =  1
SCORE:  Cumulative_reward= 234772.46 - Step_rewars (load_t= 201761.92, EVs_energy_t= 17779.09)
 - Final_rewards (EVs_energy= 10552.39, Overconsume= -381.88, Underconsume= -9456.44, Overcost= 14517.38)
Episode:1 Score:234772.45880452407


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                        
2022-01-01 00:00:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:15:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:30:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 00:45:00  0.0   0.000000   0.000000   0.000000   
2022-01-01 01:00:00  0.0   0.000000   0.000000   0.000000   
...                  ...        ...        ...        ...   
2022-06-06 04:45:00  0.0  37.308075  99.989998  37.364552   
2022-06-06 05:00:00  0.0  37.308075  99.989998  37.364552   
2022-06-06 05:15:00  0.0  37.308075  99.989998  37.364552   
2022-06-06 05:30:00  0.0  37.308075  99.989998  37.364552   
2022-06-06 05:45:00  0.0  37.308075  99.989998  37.364552   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [0, 0, 0, 0]   
...                                    ...           ...   
2022-06-06 04:45:00  [0, 9829, 9828, 9830]  [0, 0, 1, 0]   
2022-06-06 05:00:00  [0, 9829, 9828, 9830]  [0, 0, 1, 0]   
2022-06-06 05:15:00  [0, 9829, 9828, 9830]  [0, 0, 1, 0]   
2022-06-06 05:30:00  [0, 9829, 9828, 9830]  [0, 0, 1, 0]   
2022-06-06 05:45:00  [0, 9829, 9828, 9830]  [0, 0, 1, 0]   

                                     mask_truth       load  load_reward  \
time                                                                      
2022-01-01 00:00:00    [True, True, True, True]  -2.854994    -5.612381   
2022-01-01 00:15:00    [True, True, True, True]  -4.673619    -5.041353   
2022-01-01 00:30:00    [True, True, True, True]  -4.045488    -2.745406   
2022-01-01 00:45:00    [True, True, True, True]  -2.647244    -6.635503   
2022-01-01 01:00:00    [True, True, True, True]  -5.799053    -6.354202   
...                                         ...        ...          ...   
2022-06-06 04:45:00  [True, False, False, True]  -5.475365   -10.330470   
2022-06-06 05:00:00  [True, False, False, True]  -9.863517    -9.945715   
2022-06-06 05:15:00  [True, False, False, True]  -9.440286   -10.465544   
2022-06-06 05:30:00  [True, False, False, True] -10.012098   -10.824442   
2022-06-06 05:45:00  [True, False, False, True] -10.406887   -10.634823   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -5.612381  
2022-01-01 00:15:00        0.0  -5.041353  
2022-01-01 00:30:00        0.0  -2.745406  
2022-01-01 00:45:00        0.0  -6.635503  
2022-01-01 01:00:00        0.0  -6.354202  
...                        ...        ...  
2022-06-06 04:45:00        0.0 -10.330470  
2022-06-06 05:00:00        0.0  -9.945715  
2022-06-06 05:15:00        0.0 -10.465544  
2022-06-06 05:30:00        0.0 -10.824442  
2022-06-06 05:45:00        0.0 -10.634823  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()